In [15]:
import pandas as pd
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity

In [2]:
movies = pd.read_csv('../data/reduced/movies_m10_rich_pre.csv', index_col='movieId')
ratings = pd.read_csv('../data/reduced/ratings_m10.csv')

In [3]:
ratings.head(1)

userId  movieId  rating  timestamp
0       1        1     4.0  964982703

In [4]:
movies.head(1)

Unnamed: 0  tmdbId  imdbId  \
movieId                               
1                 1     862  114709   

                                                      cast       director  \
movieId                                                                     
1        ['Tom Hanks', 'Tim Allen', 'Don Rickles', 'Jim...  John Lasseter   

                                                  keywords  \
movieId                                                      
1        ['jealousy', 'toy', 'boy', 'friendship', 'frie...   

                                                  overview       title  \
movieId                                                                  
1        Woody the cowboy is young Andyâ€™s favorite to...  Toy Story    

                                                    genres  year  
movieId                                                           
1        ['Adventure', 'Animation', 'Children', 'Comedy...  1995

In [5]:
#ratings = ratings.head(200)

In [6]:
def train_test_column_split(df, group_column, split_column, y_label, train_size):
    df = df.sort_values(by=split_column, ascending=True)   
    train = pd.DataFrame(columns=df.columns)
    test = pd.DataFrame(columns=df.columns)

    for idx in df[group_column].unique():
        group = df.loc[df[group_column] == idx]

        q_user = group[group[split_column].le(group[split_column].quantile(train_size))]
        p_user = group[group[split_column].ge(group[split_column].quantile(train_size))]

        train = pd.concat([train, q_user])
        test = pd.concat([test, p_user])
    train = train.sort_index(ascending=True)
    test = test.sort_index(ascending=True)

    X_labels = [c for c in df.columns if c != y_label]

    X_train = train[X_labels]
    X_test = test[X_labels]
    y_train = train[y_label]
    y_test = test[y_label]

    return (X_train, X_test, y_train, y_test)

In [7]:
X_train, X_test, y_train, y_test = train_test_column_split(ratings, 'userId', 'timestamp', 'rating', .9)

In [8]:
X_train

userId movieId   timestamp
0          1       1   964982703
1          1       3   964981247
2          1       6   964982224
4          1      50   964982931
5          1      70   964982400
...      ...     ...         ...
81109    610  157296  1493846563
81110    610  158238  1479545219
81111    610  159093  1493847704
81112    610  164179  1493845631
81115    610  168252  1493846352

[72991 rows x 3 columns]

In [9]:
y_train

0        4.0
1        4.0
2        4.0
4        5.0
5        3.0
        ... 
81109    4.0
81110    5.0
81111    3.0
81112    5.0
81115    5.0
Name: rating, Length: 72991, dtype: float64

In [10]:
X_test

userId movieId   timestamp
3          1      47   964983815
8          1     151   964984041
9          1     157   964984100
28         1     527   964984002
31         1     553   964984153
...      ...     ...         ...
81075    610  115149  1493849607
81076    610  115210  1493849803
81105    610  142488  1493849575
81113    610  166528  1493879365
81114    610  168250  1494273047

[8621 rows x 3 columns]

In [11]:
y_test

3        5.0
8        5.0
9        5.0
28       5.0
31       5.0
        ... 
81075    5.0
81076    4.0
81105    3.5
81113    4.0
81114    5.0
Name: rating, Length: 8621, dtype: float64

In [14]:
X_train.to_csv('../data/splitted/X_train_90.csv')
X_test.to_csv('../data/splitted/X_test_90.csv')
np.save('../data/splitted/y_train_90.npy', y_train)
np.save('../data/splitted/y_test_90.npy', y_test)